In [1]:
import os
os.environ["CALITP_BQ_MAX_BYTES"] = str(800_000_000_000)
import shared_utils

import geopandas as gpd
import pandas as pd
import folium 
import branca
import datetime as dt
from siuba import *
from bus_service_utils import better_bus_utils

from rt_analysis import rt_filter_map_plot

ZERO_THIRTY_COLORSCALE = branca.colormap.step.RdYlGn_11.scale(vmin=0, vmax=35)

/opt/conda/lib/python3.9/site-packages/geopandas/_compat.py:123: UserWarning: The Shapely GEOS version (3.10.3-CAPI-1.16.1) is incompatible with the GEOS version PyGEOS was compiled with (3.10.1-CAPI-1.16.0). Conversions between both will be slow.
  warnings.warn(


In [2]:
import bb_rt_helper

In [3]:
import importlib
importlib.reload(bb_rt_helper)

<module 'bb_rt_helper' from '/home/jovyan/data-analyses/one_hundred_recs/bb_rt_helper.py'>

# 100 Recs - D5

## 1 - Corridor Improvements

In [4]:
bb_rt_helper.fm_from_bbutils?

Signature:
bb_rt_helper.fm_from_bbutils(
    ct_dist,
    category,
    get_sorted=False,
    fm_dict={},
    analysis_date=datetime.date(2022, 5, 4),
)
Docstring:
ct_dist: str, Caltrans district, formatted as in "11 - San Diego"
category: str, reccomendation category, "corridor" or "hotspot"
get_sorted: use better_bus_utils.get_sorted_transit_routes instead of 
corridor/hotspot dedicated function. Default False, override if few/no
suitable routes returned.
fm_dict: dictionary of rt_analysis.rt_filter_map_plot.RtFilterMapper instances,
if some are already loaded (for example when running for hotspot after corridor)
File:      ~/data-analyses/one_hundred_recs/bb_rt_helper.py
Type:      function


In [5]:
fm_dict = bb_rt_helper.fm_from_bbutils(ct_dist='05 - San Luis Obispo', category='corridor', analysis_date=dt.date(2022, 7, 4))

05 - San Luis Obispo corridor empty with default util, retrying with get_sorted


loading filter/mapper for 208
found parquet
loading filter/mapper for 289
no filtermapper for 289
loading filter/mapper for 296
no filtermapper for 296
{208: <rt_analysis.rt_filter_map_plot.RtFilterMapper object at 0x7fb7d070de50>}


## RT Data Notes

* Date shift for MST, routes may not match 100%
* no RT data in 2022 for Santa Cruz Metro or SLORTA

In [6]:
corr_speed_views = []
for key in fm_dict.keys():
    _m = fm_dict[key].segment_speed_map()
    corr_speed_views += [fm_dict[key].detailed_map_view.copy()]

/opt/conda/lib/python3.9/site-packages/shapely/ops.py:639: ShapelyDeprecationWarning: GeometryTypeError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:395: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:395: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [7]:
m_corr = fm_dict[208].segment_speed_map()

/opt/conda/lib/python3.9/site-packages/shapely/ops.py:639: ShapelyDeprecationWarning: GeometryTypeError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:395: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:395: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [8]:
m_corr

## Draft Corridor Recs, Monterey-Salinas Transit, D3

* Route 

## Jazz A/B, Fremont St

In [9]:
shape_id = 'B092'
stop_range = [14, 21]

In [10]:
fm_dict[208].autocorridor(shape_id=shape_id, stop_seq_range=stop_range)

In [11]:
fm_dict[208].reset_filter()

In [12]:
fm_dict[208].corridor_metrics()

{'schedule_metric_minutes': -25, 'speed_metric_minutes': 22}

In [13]:
fm_dict[208].quick_map_corridor()

In [14]:
corr_jazz = fm_dict[208].corridor.copy() # important to use .copy() here to avoid referencing the changing corridor

In [15]:
corridors = [corr_jazz]

## Route 41

In [16]:
shape_id = '41090'
stop_range = [2, 11]

In [17]:
fm_dict[208].autocorridor(shape_id=shape_id, stop_seq_range=stop_range)

In [18]:
fm_dict[208].set_filter(route_names=['41'])

In [19]:
fm_dict[208].corridor_metrics()

{'schedule_metric_minutes': -38, 'speed_metric_minutes': 369}

In [20]:
fm_dict[208].quick_map_corridor()

In [21]:
corr_41 = fm_dict[208].corridor.copy() # important to use .copy() here to avoid referencing the changing corridor

In [22]:
corridors += [corr_41]

## 2 - Hotspot Improvements

In [23]:
# without get_sorted returns mainly Metro Rail
fm_dict = bb_rt_helper.fm_from_bbutils(ct_dist='05 - San Luis Obispo', category='hotspot', fm_dict = fm_dict)

05 - San Luis Obispo hotspot empty with default util, retrying with get_sorted


loading filter/mapper for 208
loading filter/mapper for 289
no filtermapper for 289
loading filter/mapper for 296
no filtermapper for 296
{208: <rt_analysis.rt_filter_map_plot.RtFilterMapper object at 0x7fb7d070de50>}


In [24]:
hs_speed_views = []
for key in fm_dict.keys():
    _m = fm_dict[key].segment_speed_map()
    hs_speed_views += [fm_dict[key].detailed_map_view.copy()]

/opt/conda/lib/python3.9/site-packages/shapely/ops.py:639: ShapelyDeprecationWarning: GeometryTypeError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:395: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:395: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [25]:
m_hs = fm_dict[208].segment_speed_map()

/opt/conda/lib/python3.9/site-packages/shapely/ops.py:639: ShapelyDeprecationWarning: GeometryTypeError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:395: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:395: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [26]:
m_hs

# Draft Hotspot Recs, MST, D5

## Route 4 (I-405)

In [27]:
shape_id = '45027'
stop_range = [5, 7]

In [28]:
fm_dict[208].set_filter(route_names=['45'])

In [29]:
fm_dict[208].autocorridor(shape_id=shape_id, stop_seq_range=stop_range)

In [30]:
fm_dict[208].corridor_metrics()

{'schedule_metric_minutes': 0, 'speed_metric_minutes': 12}

In [31]:
fm_dict[208].quick_map_corridor()

In [32]:
hs_45 = fm_dict[208].corridor.copy()
hotspots = [hs_45]

## Map Testing

In [33]:
all_speed_segs = pd.concat(hs_speed_views)
all_corr_segs = pd.concat(corr_speed_views)
# full join to preserve all unique segments, since they can differ
# from hotspot to corridor (or indeed across operators)
all_segs = all_speed_segs >> full_join(_, all_corr_segs)

In [34]:
importlib.reload(bb_rt_helper)

<module 'bb_rt_helper' from '/home/jovyan/data-analyses/one_hundred_recs/bb_rt_helper.py'>

In [36]:
bb_rt_helper.bb_map_all(hotspots, corridors, all_segs, district = '05 - San Luis Obispo')

/home/jovyan/data-analyses/one_hundred_recs/bb_rt_helper.py:77: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

/home/jovyan/data-analyses/one_hundred_recs/bb_rt_helper.py:77: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

